This noteboook uses the SuperBuild of SimpleITK to register a previous subject scan to its corresponding initial reconstruction. The instructions for installing the SuperBuild can be found here:

https://simpleitk.readthedocs.io/en/master/building.html

It is recommended to install the SimpleITK superbuild using a virtual environment. That environment can then be used within a jupyter notebook by adding it as a kernel using the following command:

python -m ipykernel install --user --name=myenv

Where 'myenv' is the name of the environment which contains SimpleITK. The complete instructions for creating and adding a virtual environment in jupyter can be found here:

https://janakiev.com/blog/jupyter-virtual-envs/




In [1]:
import SimpleITK as sitk
import numpy as np
import nibabel as nib
import matplotlib.pyplot as plt
import os

I have created a text file called 'all_files.txt' which contains the pairs of scans that will be registered using this script. The first column of all_files.txt is the previous scan (moving image) and the second column is the initial reconstruction (fixed image). The previous scan will be elastically registered to the initial reconstruction produced in the previous step. 

In [2]:
all_files = np.loadtxt('../data/test_long.txt', dtype=str)
save_path = "../data/reference_reg_10x-varnet/"
os.makedirs(save_path, exist_ok=True)

In [3]:
print(all_files)

[['TUM04-20170309.nii' 'TUM04-20171108.nii' 'TUM04-20180103.nii']
 ['TUM04-20171108.nii' 'TUM04-20190328.nii' 'TUM04-20190523.nii']
 ['TUM04-20180618.nii' 'TUM04-20181009.nii' 'TUM04-20190328.nii']
 ['TUM20-20170928.nii' 'TUM20-20180205.nii' 'TUM20-20180402.nii']
 ['TUM10-20170316.nii' 'TUM10-20171018.nii' 'TUM10-20180122.nii']
 ['TUM10-20171018.nii' 'TUM10-20180122.nii' 'TUM10-20180307.nii']
 ['TUM15-20170531.nii' 'TUM15-20170801.nii' 'TUM15-20170816.nii']]


In [4]:
all_files[0][1]

'TUM04-20171108.nii'

In [5]:
#perform elastic registration for each pair of longitudinal scans
for idx in range(len(all_files)):

    fixed_path = f"../data/predicted/10x-varnet/nib/{all_files[idx][2][:-4]}_predicted.nii" 
    moving_path = f"../data/predicted/10x-enhanced-varnet/{all_files[idx][1][:-4]}_predicted-0.nii"
    print('previous scan:', moving_path)
    print('follow-up scan', fixed_path)
    moving = moving_path.split('/')[-1][:-16]
    fixed = fixed_path.split('/')[-1][:-14]

    previous = nib.load(moving_path).get_fdata()
    next_ = nib.load(fixed_path)
    next_affine = next_.affine
    next_ = next_.get_fdata()
    print('shape of fixed image', nib.load(fixed_path).shape)
    print('shape of moving image', nib.load(moving_path).shape)

    # Loading fixed and moving images
    fixed_image = sitk.ReadImage(fixed_path)
    moving_image = sitk.ReadImage(moving_path)

    elastixImageFilter = sitk.ElastixImageFilter()
    elastixImageFilter.SetFixedImage(fixed_image)
    elastixImageFilter.SetMovingImage(moving_image)
    parameterMapVector = sitk.VectorOfParameterMap()
    parameterMapVector.append(sitk.ReadParameterFile("../data/param_files/Par0000affine.txt"))
    parameterMapVector.append(sitk.ReadParameterFile("../data/param_files/Par0000bspline.txt"))

    elastixImageFilter.SetParameterMap(parameterMapVector)
    elastixImageFilter.Execute()

    # Save image as nifti
    registered = elastixImageFilter.GetResultImage()
    reg = sitk.GetArrayFromImage(registered)
    reg = np.swapaxes(reg,0,2)

    name_reg = "elastic_" + moving + "_" + fixed + '-2.nii'

    img = nib.Nifti1Image(reg, next_affine)
    nib.save(img, save_path + name_reg)
    sitk.WriteImage(registered,save_path + name_reg)
    print(save_path + name_reg)



previous scan: ../data/predicted/10x-enhanced-varnet/TUM04-20171108_predicted-0.nii
follow-up scan ../data/predicted/10x-varnet/nib/TUM04-20180103_predicted.nii
shape of fixed image (512, 512, 160)
shape of moving image (512, 512, 156)
Installing all components.
InstallingComponents was successful.

ELASTIX version: 5.000
Command line options from ElastixBase:
-fMask    unspecified, so no fixed mask used
-mMask    unspecified, so no moving mask used
-out      ./
-threads  unspecified, so all available threads are used
  The default value "true" is used instead.

  From elastix 4.8 it defaults to true!
This may change the behavior of your registrations considerably.

Command line options from TransformBase:
-t0       unspecified, so no initial transform used

Reading images...
Reading images took 0 ms.

  A default pyramid schedule is used.
  A default pyramid schedule is used.
  The default value "GeometricalCenter" is used instead.
Transform parameters are initialized as: [1, 0, 0, 0,

172	-1.005548	5.683638	5.340686	0.017235	0.8
173	-1.021711	6.683527	5.147788	0.016056	1.2
174	-1.021792	7.683527	4.968319	0.020609	0.9
175	-0.963417	8.683527	4.800943	0.014790	0.9
176	-1.023690	9.683527	4.644477	0.029244	0.8
177	-1.029617	10.683522	4.497888	0.023298	0.9
178	-0.997136	11.683522	4.360268	0.013892	0.8
179	-0.986009	12.683477	4.230826	0.013280	0.8
180	-1.008925	13.614372	4.117045	0.014051	0.8
181	-1.012507	14.614372	4.001444	0.017842	0.8
182	-1.032010	14.437730	4.021390	0.028707	0.8
183	-1.005430	15.437730	3.911026	0.010927	0.8
184	-1.028201	15.285792	3.927403	0.011835	0.8
185	-1.036974	15.109224	3.946607	0.020493	0.8
186	-1.018174	16.109220	3.840256	0.013033	0.9
187	-1.010339	17.109219	3.739487	0.021052	0.9
188	-1.010262	16.932562	3.756902	0.018461	0.8
189	-1.024935	17.932562	3.660404	0.016280	0.8
190	-1.019032	18.931024	3.568877	0.018710	0.8
191	-0.972790	19.931024	3.481685	0.022592	0.9
192	-1.014850	20.931023	3.398651	0.022369	0.9
193	-1.013364	21.931023	3.319486	0.0175

408	-1.024798	119.145433	1.016865	0.016680	0.8
409	-1.014642	118.977646	1.018083	0.012227	1.3
410	-0.986856	118.800990	1.019370	0.019163	0.8
411	-0.987471	119.800989	1.012130	0.028006	0.9
412	-1.016792	120.800989	1.004992	0.012095	0.8
413	-1.021969	121.800989	0.997955	0.022700	0.9
414	-1.008194	121.624334	0.999191	0.012504	0.8
415	-1.053844	121.447677	1.000430	0.015227	0.8
416	-1.007792	121.271019	1.001672	0.021532	0.9
417	-1.037255	122.042809	0.996268	0.018666	0.8
418	-1.029828	121.866152	0.997500	0.017586	0.8
419	-1.047919	122.866152	0.990566	0.015851	0.8
420	-0.996749	123.866152	0.983728	0.024241	0.9
421	-1.012878	124.866152	0.976984	0.011870	0.9
422	-1.007221	125.866152	0.970332	0.015197	0.9
423	-1.033018	125.704967	0.971398	0.014608	0.9
424	-0.996083	125.528310	0.972569	0.018561	1.4
425	-1.016798	126.528310	0.965977	0.022558	0.8
426	-0.975139	127.528310	0.959473	0.011703	0.9
427	-0.989753	128.528310	0.953056	0.018037	1.0
428	-1.035234	128.351652	0.954184	0.020998	0.9
429	-1.004775

168	-0.942642	61.872785	0.760973	0.018918	0.8
169	-0.953845	61.537171	0.764067	0.024862	1.0
170	-0.934859	62.533370	0.754955	0.018591	1.1
171	-0.918041	63.533242	0.746026	0.018944	0.8
172	-0.932811	63.793301	0.743738	0.021662	0.8
173	-0.963122	64.791268	0.735086	0.032032	0.8
174	-0.902678	65.791267	0.726616	0.036212	0.8
175	-0.965868	65.444151	0.729534	0.019844	0.9
176	-0.906576	65.097034	0.732475	0.042209	0.8
177	-0.941247	66.096885	0.724067	0.024335	0.8
178	-0.920196	66.194222	0.723258	0.036791	0.8
179	-0.937700	67.194222	0.715058	0.035160	0.8
180	-0.908801	68.194221	0.707041	0.028788	0.9
181	-0.927740	69.193708	0.699206	0.019850	0.8
182	-0.918122	68.855851	0.701835	0.024537	0.9
183	-0.941886	68.509309	0.704552	0.026124	0.9
184	-0.922612	68.214621	0.706879	0.041434	0.8
185	-0.928078	69.214619	0.699044	0.028570	0.8
186	-0.929302	70.214185	0.691383	0.022059	0.9
187	-0.945169	69.867074	0.694024	0.029005	0.8
188	-0.943851	69.519957	0.696686	0.031008	0.9
189	-0.875233	69.180899	0.699305	0

402	-0.946423	138.740904	0.394789	0.019947	0.8
403	-0.981540	138.393823	0.395649	0.033317	0.9
404	-0.947180	138.047235	0.396511	0.025085	4.6
405	-0.922520	137.716716	0.397337	0.023754	0.9
406	-0.901894	138.716661	0.394849	0.028381	0.8
407	-0.917544	138.937427	0.394304	0.025027	0.9
408	-0.894125	139.937307	0.391854	0.032574	0.8
409	-0.931402	140.937307	0.389434	0.024260	0.9
410	-0.911969	140.590296	0.390271	0.033864	0.8
411	-0.918252	141.585298	0.387882	0.027865	0.9
412	-0.931397	141.284485	0.388601	0.012551	0.8
413	-0.912768	141.586799	0.387879	0.027923	0.8
414	-0.936214	141.454746	0.388194	0.032841	0.9
415	-0.947325	142.454745	0.385819	0.023019	0.9
416	-0.930098	142.107629	0.386640	0.024378	0.8
417	-0.946062	141.760811	0.387464	0.024098	0.8
418	-0.948682	142.731153	0.385168	0.031888	0.8
419	-0.927470	142.385395	0.385983	0.029208	0.8
420	-0.940056	143.385394	0.383635	0.028023	0.8
421	-0.901001	144.363536	0.381366	0.015599	0.9
422	-0.916979	144.016429	0.382168	0.023626	0.8
423	-0.929283

...

1087	-0.493281	142.925637	0.012599	16.1
1088	-0.763981	142.853501	0.008218	16.1
1089	-0.370937	142.781462	0.004973	16.1
1090	-0.521244	142.709519	0.011320	15.5
1091	-1.060574	142.637674	0.011680	15.5
1092	-0.854893	142.565924	0.007718	15.5
1093	-1.214036	142.494271	0.022926	15.6
1094	-0.678405	142.422714	0.007516	15.6
1095	-0.647717	142.351252	0.007859	15.7
1096	-0.083924	142.279886	0.003323	15.5
1097	-1.101521	142.208616	0.011701	15.6
1098	-0.732366	142.137440	0.010660	15.6
1099	-0.852272	142.066360	0.007185	15.6
1100	-0.767365	141.995374	0.007635	15.7
1101	-0.728942	141.924483	0.007819	16.0
1102	-0.727549	141.853685	0.008625	15.8
1103	-0.600841	141.782983	0.007392	15.5
1104	-0.788325	141.712373	0.010631	15.6
1105	-0.620333	141.641858	0.006878	15.8
1106	-0.588973	141.571436	0.006773	15.9
1107	-0.734105	141.501108	0.009652	15.7
1108	-1.105799	141.430872	0.012905	15.7
1109	-0.243450	141.360730	0.007458	15.5
1110	-0.463273	141.290680	0.005063	15.5
1111	-0.596294	141.220722	0.007730	15.7


1295	-1.053245	129.738463	0.011782	15.7
1296	-0.957717	129.682734	0.009980	15.8
1297	-0.935723	129.627068	0.011895	16.0
1298	-0.720303	129.571466	0.009584	15.5
1299	-0.637414	129.515927	0.005879	15.5
1300	-0.755418	129.460452	0.008399	15.7
1301	-0.155296	129.405040	0.005022	15.6
1302	-0.456223	129.349692	0.006338	15.7
1303	-0.469286	129.294406	0.009741	15.5
1304	-0.377487	129.239183	0.005163	15.6
1305	-0.293604	129.184024	0.006102	15.5
1306	-0.010399	129.128927	0.001600	15.6
1307	-0.793670	129.073892	0.006932	15.6
1308	-0.762289	129.018921	0.011619	15.6
1309	-0.454308	128.964011	0.005619	15.8
1310	-1.027864	128.909164	0.010230	15.8
1311	-0.909976	128.854379	0.011390	15.6
1312	-0.322173	128.799656	0.009868	15.5
1313	-0.624787	128.744995	0.006464	15.5
1314	-1.120263	128.690396	0.019335	15.5
1315	-0.596700	128.635858	0.007483	15.7
1316	-0.074104	128.581382	0.003839	15.6
1317	-0.678205	128.526968	0.006646	15.6
1318	-0.964924	128.472615	0.009328	15.7
1319	-0.623470	128.418323	0.007344	15.8


1503	-0.473982	119.365104	0.005841	16.1
1504	-0.729129	119.320476	0.008495	16.0
1505	-1.006914	119.275893	0.010471	15.9
1506	-0.442661	119.231353	0.005298	15.5
1507	-1.131886	119.186859	0.015167	15.6
1508	-0.545892	119.142408	0.005547	15.6
1509	-1.102467	119.098002	0.009748	15.6
1510	-0.727645	119.053639	0.006790	15.7
1511	-0.642626	119.009321	0.010545	15.5
1512	-0.967466	118.965047	0.014449	15.6
1513	-0.543520	118.920816	0.009233	15.5
1514	-1.116378	118.876630	0.014070	15.4
1515	-0.869677	118.832487	0.009331	15.6
1516	-0.696071	118.788388	0.006676	15.6
1517	-0.174413	118.744332	0.005586	16.1
1518	-0.868519	118.700320	0.011121	15.9
1519	-0.340583	118.656352	0.007272	15.6
1520	-0.365736	118.612427	0.006899	15.4
1521	-0.331622	118.568545	0.006205	15.6
1522	-0.665217	118.524706	0.007240	15.6
1523	-1.136996	118.480911	0.012084	15.6
1524	-0.390943	118.437159	0.005807	15.5
1525	-0.461345	118.393450	0.006386	15.6
1526	-1.121339	118.349784	0.010734	15.6
1527	-0.846157	118.306160	0.008555	15.6


1711	-0.000107	110.944323	0.000032	15.7
1712	-0.771729	110.907603	0.007617	16.2
1713	-1.041454	110.870915	0.015486	15.7
1714	-0.929241	110.834259	0.008316	15.7
1715	-0.710246	110.797636	0.006448	15.6
1716	-1.031647	110.761045	0.009842	15.6
1717	-0.584827	110.724486	0.009500	15.7
1718	-0.891369	110.687959	0.008362	15.7
1719	-0.962839	110.651465	0.009170	15.6
1720	-0.521846	110.615002	0.006373	15.6
1721	-0.866351	110.578572	0.008271	15.6
1722	-0.704277	110.542173	0.008867	15.5
1723	-0.701508	110.505807	0.006322	15.5
1724	-0.535930	110.469472	0.008352	15.7
1725	-1.061229	110.433169	0.014076	15.8
1726	-0.646013	110.396898	0.006513	15.8
1727	-0.668250	110.360659	0.007448	15.6
1728	-0.588271	110.324451	0.005930	15.6
1729	-0.750808	110.288276	0.007264	16.6
1730	-0.430258	110.252131	0.006363	16.1
1731	-0.733152	110.216019	0.006453	15.6
1732	-0.828332	110.179937	0.009126	15.6
1733	-0.441347	110.143888	0.004247	15.7
1734	-0.702902	110.107869	0.007354	15.6
1735	-0.713817	110.071882	0.009221	15.6


1919	-0.569326	103.941547	0.007257	15.9
1920	-0.903632	103.910686	0.009275	15.8
1921	-1.144192	103.879849	0.012413	16.0
1922	-0.538216	103.849036	0.007314	15.6
1923	-0.962739	103.818248	0.010387	15.5
1924	-0.762170	103.787484	0.007097	15.7
1925	-0.433919	103.756744	0.004769	15.6
1926	-0.792124	103.726029	0.008648	15.7
1927	-0.714559	103.695338	0.008935	15.5
1928	-1.054813	103.664671	0.011966	15.5
1929	-1.116214	103.634028	0.016042	15.6
1930	-0.875181	103.603409	0.012301	15.4
1931	-0.859760	103.572814	0.011609	15.7
1932	-0.677495	103.542244	0.008013	15.9
1933	-0.937643	103.511698	0.010930	15.9
1934	-0.541531	103.481175	0.006399	16.0
1935	-0.665777	103.450677	0.008452	15.6
1936	-0.797625	103.420202	0.008185	15.6
1937	-1.100016	103.389752	0.010580	15.7
1938	-0.451290	103.359325	0.004315	15.6
1939	-0.613373	103.328922	0.005973	15.5
1940	-1.052550	103.298543	0.012065	15.7
1941	-0.838877	103.268188	0.009308	15.6
1942	-0.382134	103.237857	0.005914	15.6
1943	-0.478819	103.207549	0.005937	15.7
